<a href="https://colab.research.google.com/github/sunshineluyao/ic-gov-visualization/blob/main/code/Data_Visualization_GoogleColab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Part I Set up

In [2]:
pip install plotapi

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
pip install igviz

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 15.3 MB 5.2 MB/s 
     |████████████████████████████████| 1.6 MB 8.0 MB/s 
  Attempting uninstall: plotly
    Found existing installation: plotly 5.5.0
    Uninstalling plotly-5.5.0:
      Successfully uninstalled plotly-5.5.0


In [5]:
pip install pyecharts

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 135 kB 4.6 MB/s 
     |████████████████████████████████| 139 kB 9.9 MB/s 


In [17]:
import collections
import json
import os
import pickle
import string
import warnings
from multiprocessing.pool import ThreadPool
from operator import itemgetter

import igviz as ig
import networkx as nx
import nltk # https://realpython.com/nltk-nlp-python/
import pandas as pd
import plotapi
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import pyecharts.options as opts
import regex
import requests
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from plotapi import SplitChord, Terminus
from plotly.subplots import make_subplots
from pyecharts.charts import WordCloud
from tqdm import tqdm

warnings.filterwarnings('ignore')
nltk.download('stopwords') 

Your PlotAPI API key has been saved in your local environment. You will not need to set it again.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [22]:
#@title Get your Plot API Key before moving forward
PlotAPI = "b0368160-7e02-4566-9dec-1829bd5b070b" #@param {type:"string"}


In [23]:
plotapi.api_key("b0368160-7e02-4566-9dec-1829bd5b070b")

Your PlotAPI API key has been saved in your local environment. You will not need to set it again.


In [18]:
# see all the figure templates: https://plotly.com/python/templates/
pio.templates

Templates configuration
-----------------------
    Default template: 'ggplot2'
    Available templates:
        ['ggplot2', 'seaborn', 'simple_white', 'plotly',
         'plotly_white', 'plotly_dark', 'presentation', 'xgridoff',
         'ygridoff', 'gridon', 'none']

In [19]:
pio.templates.default = 'ggplot2'

In [20]:
# mount google drive
from google.colab import drive

drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [21]:
# print the current directory
!pwd

/content/drive/My Drive/ic-gov-visualization


In [11]:
#@title path
#create a project folder and identify the path
path = "/content/drive/MyDrive/ic-gov-visualization" #@param {type:"string"}


In [12]:
#go to your project folder 
%cd /content/drive/MyDrive/ic-gov-visualization

/content/drive/MyDrive/ic-gov-visualization


In [13]:
# print the current directory again to make sure that you are in the project folder
!pwd  

/content/drive/MyDrive/ic-gov-visualization


In [14]:
import pandas as pd
import numpy as np

# Part II: Query and Process Data

In [28]:
base_url = 'https://ic-api.internetcomputer.org'

In [29]:
# get total proposal counts
res = requests.get(f'{base_url}/api/nns/proposals-count')
proposals_count = json.loads(res.text)['proposals_count']

print(f'Total Proposals: {proposals_count}')


fetched: proposal 6908
fetched: proposal 6828
fetched: proposal 6911
fetched: proposal 6832
fetched: proposal 6913
fetched: proposal 6912
fetched: proposal 6845fetched: proposal 6839fetched: proposal 6850
fetched: proposal 6844

fetched: proposal 6916
fetched: proposal 6905fetched: proposal 6914
fetched: proposal 6915
fetched: proposal 6917
fetched: proposal 6840
fetched: proposal 6907


fetched: proposal 6910
fetched: proposal 6919fetched: proposal 6920

fetched: proposal 6918
fetched: proposal 6921
fetched: proposal 6922
fetched: proposal 6860fetched: proposal 6841

fetched: proposal 6861fetched: proposal 6857fetched: proposal 6859


fetched: proposal 6929
fetched: proposal 6926
fetched: proposal 6933fetched: proposal 6927

fetched: proposal 6925
fetched: proposal 6934fetched: proposal 6924fetched: proposal 6930
fetched: proposal 6928fetched: proposal 6935fetched: proposal 6851
fetched: proposal 6932
fetched: proposal 6931
fetched: proposal 6863

fetched: proposal 6923

fetched: prop

In [31]:
# fetch proposals
def get_proposal(id):
    url = base_url + '/api/v3/proposals/' + str(id)
    res = requests.get(url)
    res_dict = json.loads(res.text)
    return res_dict


def get_neuron(id):
    url = f'https://ic-api.internetcomputer.org/api/v3/neurons/{id}'
    res = requests.get(url)
    res_dict = json.loads(res.text)
    return res_dict


fetched: proposal 11321
fetched: proposal 11331
fetched: proposal 11326
fetched: proposal 11333
fetched: proposal 11336
fetched: proposal 11323
fetched: proposal 11334
fetched: proposal 11340
fetched: proposal 11352
fetched: proposal 11338
fetched: proposal 11327
fetched: proposal 11343
fetched: proposal 11344
fetched: proposal 11342
fetched: proposal 11347
fetched: proposal 11349


In [32]:
proposals = []
proposal_ids = [i for i in range(proposals_count)]


def dummy(id):
    res = get_proposal(id)
    proposals.append(dict(
        id=id,
        data=res
    ))
    print(f'fetched: proposal {id}')


# enable multithreading for faster download
pool = ThreadPool(50)

pool.imap_unordered(dummy, proposal_ids)


fetched: proposal 12193
fetched: proposal 12201
fetched: proposal 12200
fetched: proposal 12199
fetched: proposal 12192
fetched: proposal 12196
fetched: proposal 12207
fetched: proposal 12197
fetched: proposal 12206
fetched: proposal 12194
fetched: proposal 12205
fetched: proposal 12204
fetched: proposal 12203
fetched: proposal 12202
fetched: proposal 12198
fetched: proposal 12211
fetched: proposal 12209
fetched: proposal 12210
fetched: proposal 12212
fetched: proposal 12208fetched: proposal 12215
fetched: proposal 12213
fetched: proposal 12217
fetched: proposal 12224
fetched: proposal 12222
fetched: proposal 12220
fetched: proposal 12230

fetched: proposal 12214
fetched: proposal 12225
fetched: proposal 12226
fetched: proposal 12216fetched: proposal 12221

fetched: proposal 12231
fetched: proposal 12227
fetched: proposal 12232
fetched: proposal 12223
fetched: proposal 12219
fetched: proposal 12218
fetched: proposal 12235
fetched: proposal 12228
fetched: proposal 12234fetched: proposal

fetched: proposal 12407
fetched: proposal 12429
fetched: proposal 12434
fetched: proposal 12432fetched: proposal 12440
fetched: proposal 12435

fetched: proposal 12444fetched: proposal 12447
fetched: proposal 12442fetched: proposal 12450


fetched: proposal 12426
fetched: proposal 12437


In [34]:
# create an empty pickle file
import os
filename = "data/nns_data_raw.pkl"
os.makedirs(os.path.dirname(filename), exist_ok=True)

fetched: proposal 3866
fetched: proposal 3847
fetched: proposal 3864
fetched: proposal 18331
fetched: proposal 18327fetched: proposal 18333
fetched: proposal 18332

fetched: proposal 18330
fetched: proposal 18328fetched: proposal 18329
fetched: proposal 3873



In [35]:
# dump the data to the pickle file
pickle.dump(proposals, open('data/nns_data_raw.pkl', 'wb'))

fetched: proposal 3892
fetched: proposal 3891
fetched: proposal 3890
fetched: proposal 3883
fetched: proposal 3905
fetched: proposal 3865
fetched: proposal 3874
fetched: proposal 3897
fetched: proposal 18373
fetched: proposal 3907
fetched: proposal 3885
fetched: proposal 3881
fetched: proposal 18380
fetched: proposal 18382
fetched: proposal 3872
fetched: proposal 3887
fetched: proposal 3900fetched: proposal 18387fetched: proposal 18391


fetched: proposal 3906
fetched: proposal 18388
fetched: proposal 18392
fetched: proposal 18385
fetched: proposal 18384
fetched: proposal 18386
fetched: proposal 18390
fetched: proposal 3910
fetched: proposal 18394
fetched: proposal 18393
fetched: proposal 18389
fetched: proposal 18396
fetched: proposal 18397
fetched: proposal 3911
fetched: proposal 3913
fetched: proposal 18395
fetched: proposal 3912
fetched: proposal 18407
fetched: proposal 18405
fetched: proposal 18410
fetched: proposal 18401
fetched: proposal 18404
fetched: proposal 3903
fetched: pro

In [36]:
# sort data by proposal id
data = pickle.load(open('data/nns_data_raw.pkl', 'rb'))
data.sort(key=itemgetter('id'))
json.dump(data, open('data/proposals.json', 'w'))

fetched: proposal 5324
fetched: proposal 20658
fetched: proposal 5335
fetched: proposal 20659fetched: proposal 20675
fetched: proposal 20665
fetched: proposal 20667
fetched: proposal 5331
fetched: proposal 20662fetched: proposal 5328fetched: proposal 5336fetched: proposal 20696


fetched: proposal 20670
fetched: proposal 20686fetched: proposal 20702fetched: proposal 20674
fetched: proposal 20660fetched: proposal 20683fetched: proposal 20663
fetched: proposal 20668
fetched: proposal 20705fetched: proposal 20677
fetched: proposal 20661
fetched: proposal 20690


fetched: proposal 20698
fetched: proposal 20693

fetched: proposal 5323

fetched: proposal 20681
fetched: proposal 20672
fetched: proposal 20706fetched: proposal 20666
fetched: proposal 20699
fetched: proposal 20692
fetched: proposal 20680
fetched: proposal 20688
fetched: proposal 20689
fetched: proposal 20707
fetched: proposal 5299fetched: proposal 20701
fetched: proposal 20673



fetched: proposal 20691
fetched: proposal 5343fet

In [37]:
# filter empty data and save the data as json files
proposals_no_empty = []

for item in data:
    if (item['data'].get('code') != 404):
        proposals_no_empty.append(
            item['data']
        )
json.dump(proposals_no_empty, open('data/proposals_no_empty.json', 'w'))


fetched: proposal 5694
fetched: proposal 21268
fetched: proposal 21269
fetched: proposal 21266
fetched: proposal 21261
fetched: proposal 5687
fetched: proposal 5717
fetched: proposal 21267
fetched: proposal 5701
fetched: proposal 5689
fetched: proposal 5691
fetched: proposal 5693fetched: proposal 21270
fetched: proposal 21276
fetched: proposal 21271

fetched: proposal 5696
fetched: proposal 21274
fetched: proposal 5703
fetched: proposal 5698
fetched: proposal 5706
fetched: proposal 21275
fetched: proposal 5718
fetched: proposal 21282
fetched: proposal 21279
fetched: proposal 21277
fetched: proposal 5705
fetched: proposal 5699
fetched: proposal 21281
fetched: proposal 5714
fetched: proposal 5719fetched: proposal 21284
fetched: proposal 21278

fetched: proposal 21273
fetched: proposal 21280
fetched: proposal 5707
fetched: proposal 5704
fetched: proposal 5711
fetched: proposal 21283
fetched: proposal 5726
fetched: proposal 21289
fetched: proposal 21288
fetched: proposal 5715
fetched: prop

In [65]:
# read the json file data as pandas dataframe
df = pd.read_json('data/proposals_no_empty.json')
df

fetched: proposal 31122
fetched: proposal 31132
fetched: proposal 31113
fetched: proposal 63790
fetched: proposal 31134
fetched: proposal 31131
fetched: proposal 31163
fetched: proposal 63788
fetched: proposal 63797
fetched: proposal 31162fetched: proposal 63789
fetched: proposal 63800

fetched: proposal 63791
fetched: proposal 63823
fetched: proposal 63798
fetched: proposal 63803
fetched: proposal 63793
fetched: proposal 31159
fetched: proposal 63795
fetched: proposal 63818
fetched: proposal 31160
fetched: proposal 31164
fetched: proposal 63813fetched: proposal 63809
fetched: proposal 63794
fetched: proposal 63792

fetched: proposal 63801
fetched: proposal 31139
fetched: proposal 63802
fetched: proposal 63807
fetched: proposal 63805
fetched: proposal 63804
fetched: proposal 63827
fetched: proposal 63824
fetched: proposal 31150
fetched: proposal 63830fetched: proposal 31141
fetched: proposal 63806
fetched: proposal 63814
fetched: proposal 63817

fetched: proposal 63810fetched: proposal

action   action_nns_function  deadline_timestamp_seconds  \
0     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
1     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
2     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
3     ExecuteNnsFunction        NnsRootUpgrade                         NaN   
4     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
...                  ...                   ...                         ...   
5530  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5531  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5532  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5533  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5534  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   

      decided_timestamp_seconds  executed_timestamp_seconds  \
0                    1620340878                  1620340878   
1                    1620340965                  1620340965   
2                    1620341025                  1620341025   
3                    1620341096                  1620341110   
4                    1620341144                  1620341144   
...                         ...                         ...   
5530                 1630591822                  1630591822   
5531                 1630592475                  1630592475   
5532                 1630593020                  1630593020   
5533                 1630593622                  1630593622   
5534                 1630594275                  1630594275   

      failed_timestamp_seconds    id  \
0                          0.0     1   
1                          0.0     2   
2                          0.0     3   
3                          0.0     4   
4                          0.0     5   
...                        ...   ...   
5530                       0.0  4829   
5531                       0.0  4830   
5532                       0.0  4831   
5533                       0.0  4832   
5534                       0.0  4833   

                                  known_neurons_ballots  \
0                                                    []   
1                                                    []   
2                                                    []   
3                                                    []   
4                                                    []   
...                                                 ...   
5530  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5531  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5532  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5533  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5534  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   

                                           latest_tally  \
0     {'no': 0, 'timestamp_seconds': 1620340878, 'to...   
1     {'no': 0, 'timestamp_seconds': 1620340965, 'to...   
2     {'no': 0, 'timestamp_seconds': 1620341025, 'to...   
3     {'no': 0, 'timestamp_seconds': 1620341096, 'to...   
4     {'no': 0, 'timestamp_seconds': 1620341144, 'to...   
...                                                 ...   
5530  {'no': 0, 'timestamp_seconds': 1630591822, 'to...   
5531  {'no': 0, 'timestamp_seconds': 1630592475, 'to...   
5532  {'no': 0, 'timestamp_seconds': 1630593020, 'to...   
5533  {'no': 0, 'timestamp_seconds': 1630593622, 'to...   
5534  {'no': 0, 'timestamp_seconds': 1630594275, 'to...   

                                                payload  ...  proposer  \
0     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
1     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
2     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
3                                                    {}  ...        35   
4     {'arg': [], 'authz_changes': [], 'canister_id'...

fetched: proposal 31216
fetched: proposal 63915fetched: proposal 63894
fetched: proposal 63924
fetched: proposal 31194

fetched: proposal 63923
fetched: proposal 31210
fetched: proposal 63898
fetched: proposal 63902
fetched: proposal 31239
fetched: proposal 63892
fetched: proposal 63914
fetched: proposal 63917
fetched: proposal 31237
fetched: proposal 31241
fetched: proposal 31240
fetched: proposal 63921fetched: proposal 63919

fetched: proposal 33019

fetched: proposal 67024
fetched: proposal 67034
fetched: proposal 33033
fetched: proposal 67038
fetched: proposal 67033
fetched: proposal 67029
fetched: proposal 67041
fetched: proposal 67020
fetched: proposal 32982
fetched: proposal 67039
fetched: proposal 67022
fetched: proposal 66999
fetched: proposal 67044
fetched: proposal 67061
fetched: proposal 33002
fetched: proposal 67050fetched: proposal 33005

fetched: proposal 67062
fetched: proposal 67045
fetched: proposal 67027
fetched: proposal 32986
fetched: proposal 67059
fetched: propos

In [110]:
df.to_csv("proposals_no_empty.csv")
df.to_pickle("proposals_no_empty.pkl")


fetched: proposal 90441fetched: proposal 90438fetched: proposal 90445


fetched: proposal 90436fetched: proposal 90433
fetched: proposal 90444
fetched: proposal 90442
fetched: proposal 90455
fetched: proposal 90450

fetched: proposal 90448fetched: proposal 90447
fetched: proposal 90435
fetched: proposal 90446
fetched: proposal 90459
fetched: proposal 90458fetched: proposal 90476
fetched: proposal 90468
fetched: proposal 90457
fetched: proposal 90437
fetched: proposal 90464
fetched: proposal 90451
fetched: proposal 90465fetched: proposal 90431

fetched: proposal 90440
fetched: proposal 90452fetched: proposal 90454
fetched: proposal 90460
fetched: proposal 90462fetched: proposal 90473fetched: proposal 90467

fetched: proposal 90461fetched: proposal 90479
fetched: proposal 90478
fetched: proposal 90463fetched: proposal 90449



fetched: proposal 90474
fetched: proposal 90471fetched: proposal 90469




fetched: proposal 90489
fetched: proposal 90485
fetched: proposal 90490
fetched: propos

In [639]:
df = pd.read_pickle("proposals_no_empty.pkl")
df

action   action_nns_function  deadline_timestamp_seconds  \
0     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
1     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
2     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
3     ExecuteNnsFunction        NnsRootUpgrade                         NaN   
4     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
...                  ...                   ...                         ...   
5530  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5531  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5532  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5533  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5534  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   

      decided_timestamp_seconds  executed_timestamp_seconds  \
0                    1620340878                  1620340878   
1                    1620340965                  1620340965   
2                    1620341025                  1620341025   
3                    1620341096                  1620341110   
4                    1620341144                  1620341144   
...                         ...                         ...   
5530                 1630591822                  1630591822   
5531                 1630592475                  1630592475   
5532                 1630593020                  1630593020   
5533                 1630593622                  1630593622   
5534                 1630594275                  1630594275   

      failed_timestamp_seconds    id  \
0                          0.0     1   
1                          0.0     2   
2                          0.0     3   
3                          0.0     4   
4                          0.0     5   
...                        ...   ...   
5530                       0.0  4829   
5531                       0.0  4830   
5532                       0.0  4831   
5533                       0.0  4832   
5534                       0.0  4833   

                                  known_neurons_ballots  \
0                                                    []   
1                                                    []   
2                                                    []   
3                                                    []   
4                                                    []   
...                                                 ...   
5530  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5531  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5532  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5533  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5534  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   

                                           latest_tally  \
0     {'no': 0, 'timestamp_seconds': 1620340878, 'to...   
1     {'no': 0, 'timestamp_seconds': 1620340965, 'to...   
2     {'no': 0, 'timestamp_seconds': 1620341025, 'to...   
3     {'no': 0, 'timestamp_seconds': 1620341096, 'to...   
4     {'no': 0, 'timestamp_seconds': 1620341144, 'to...   
...                                                 ...   
5530  {'no': 0, 'timestamp_seconds': 1630591822, 'to...   
5531  {'no': 0, 'timestamp_seconds': 1630592475, 'to...   
5532  {'no': 0, 'timestamp_seconds': 1630593020, 'to...   
5533  {'no': 0, 'timestamp_seconds': 1630593622, 'to...   
5534  {'no': 0, 'timestamp_seconds': 1630594275, 'to...   

                                                payload  ...  proposer  \
0     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
1     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
2     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
3                                                    {}  ...        35   
4     {'arg': [], 'authz_changes': [], 'canister_id'...

In [112]:
# display interaction tables: https://colab.research.google.com/notebooks/data_table.ipynb#scrollTo=IdBulJJa8Jta
from google.colab import data_table
data_table.DataTable(df, include_index=False, num_rows_per_page=10)

# Part III Visualizations

## 3.1. Wordcloud - Proposal Summary

In [71]:
with open('data/proposal_summary_text.txt', 'w') as f:
    f.write(' '.join(list(df['summary'].values)))

fetched: proposal 72271
fetched: proposal 72279
fetched: proposal 72277
fetched: proposal 72278
fetched: proposal 36384
fetched: proposal 72284
fetched: proposal 72283
fetched: proposal 72280
fetched: proposal 36361


In [74]:
# cleaning data for wordcloud
df_wordcloud = df[['topic', 'summary']]
df_wordcloud = df_wordcloud.groupby('topic').aggregate(' '.join).reset_index()
df_wordcloud.to_csv('data/topic_summary_joined.csv')

fetched: proposal 36891
fetched: proposal 36856
fetched: proposal 73009
fetched: proposal 72995
fetched: proposal 36893
fetched: proposal 36906
fetched: proposal 72967
fetched: proposal 72928
fetched: proposal 72991
fetched: proposal 36895
fetched: proposal 73012fetched: proposal 72978fetched: proposal 72997fetched: proposal 73006
fetched: proposal 73007

fetched: proposal 72996
fetched: proposal 36928
fetched: proposal 73003
fetched: proposal 36869

fetched: proposal 73018
fetched: proposal 36904fetched: proposal 36890
fetched: proposal 73005

fetched: proposal 72999
fetched: proposal 36908
fetched: proposal 72900
fetched: proposal 73030fetched: proposal 36900
fetched: proposal 73013

fetched: proposal 36910fetched: proposal 73038fetched: proposal 73010


fetched: proposal 72989
fetched: proposal 73022

fetched: proposal 36902
fetched: proposal 72992
fetched: proposal 73019fetched: proposal 73014
fetched: proposal 73024
fetched: proposal 36896

fetched: proposal 36915
fetched: proposa

In [75]:
import nltk
nltk.download('punkt')

fetched: proposal 73855
fetched: proposal 37367
fetched: proposal 73795
fetched: proposal 73857
fetched: proposal 73835
fetched: proposal 37373
fetched: proposal 73858
fetched: proposal 73846
fetched: proposal 73824fetched: proposal 73844fetched: proposal 73861
fetched: proposal 73816
fetched: proposal 37298
fetched: proposal 73856
fetched: proposal 37336

fetched: proposal 73840
fetched: proposal 73837
fetched: proposal 73829
fetched: proposal 37361
fetched: proposal 37359
fetched: proposal 73874fetched: proposal 37303
fetched: proposal 73834
fetched: proposal 37346
fetched: proposal 73869
fetched: proposal 37323

fetched: proposal 37356
fetched: proposal 37365
fetched: proposal 73842
fetched: proposal 37315fetched: proposal 73871
fetched: proposal 37371fetched: proposal 73879
fetched: proposal 73872

fetched: proposal 73870
fetched: proposal 73873
fetched: proposal 37390
fetched: proposal 37330
fetched: proposal 73864
fetched: proposal 37284
fetched: proposal 73862
fetched: proposal 

[nltk_data] Downloading package punkt to /root/nltk_data...


fetched: proposal 73939
fetched: proposal 73960
fetched: proposal 73941
fetched: proposal 73951
fetched: proposal 73930
fetched: proposal 73923fetched: proposal 37415
fetched: proposal 73944fetched: proposal 73946
fetched: proposal 37426fetched: proposal 73935
fetched: proposal 73937
fetched: proposal 73952

fetched: proposal 73957

fetched: proposal 73959
fetched: proposal 73969

fetched: proposal 73961
fetched: proposal 73976
fetched: proposal 73934
fetched: proposal 73958
fetched: proposal 73971fetched: proposal 73963

fetched: proposal 37403

fetched: proposal 73955

fetched: proposal 73925fetched: proposal 37362
fetched: proposal 37387
fetched: proposal 73943
fetched: proposal 73967
fetched: proposal 37409fetched: proposal 37434
fetched: proposal 73964
fetched: proposal 37435fetched: proposal 73962
fetched: proposal 73954
fetched: proposal 37386
fetched: proposal 37407
fetched: proposal 37430
fetched: proposal 73968

fetched: proposal 37385

fetched: proposal 37406
fetched: propos

[nltk_data]   Package punkt is already up-to-date!


True

fetched: proposal 74306fetched: proposal 37548fetched: proposal 74318fetched: proposal 74302

fetched: proposal 74324
fetched: proposal 74287fetched: proposal 74307
fetched: proposal 74331

fetched: proposal 37607
fetched: proposal 74308fetched: proposal 37608

fetched: proposal 74310
fetched: proposal 37591
fetched: proposal 74301fetched: proposal 74314

fetched: proposal 74327
fetched: proposal 74283
fetched: proposal 37539
fetched: proposal 74334fetched: proposal 74319
fetched: proposal 37625

fetched: proposal 74332

fetched: proposal 37621
fetched: proposal 74293
fetched: proposal 74311
fetched: proposal 37614fetched: proposal 74321
fetched: proposal 37598
fetched: proposal 74320
fetched: proposal 37568
fetched: proposal 74323
fetched: proposal 74326
fetched: proposal 74335

fetched: proposal 37590
fetched: proposal 37610fetched: proposal 37583
fetched: proposal 74297
fetched: proposal 37632fetched: proposal 74317

fetched: proposal 74316
fetched: proposal 37599fetched: proposal 7

In [53]:
# remove non-utf8 characters
def remove_non_utf8(x: str):
    x = x.encode('utf-8', errors='ignore').decode('utf-8')
    x = regex.sub(r'[^\x00-\x7f]', u'', x)
    x = regex.sub(r"http\S+", "", x)
    x = x.translate(str.maketrans('', '', string.punctuation))
    x = word_tokenize(x)
    x = [word for word in x if not word in stopwords.words('english')]

    return (" ").join(x)

df_wordcloud['summary'] = df_wordcloud['summary'].apply(remove_non_utf8)
df_wordcloud.to_csv('data/topic_summary_joined.csv')

Streaming output truncated to the last 5000 lines.
fetched: proposal 41870
fetched: proposal 17997

fetched: proposal 41835
fetched: proposal 18043
fetched: proposal 18031
fetched: proposal 41853
fetched: proposal 41865
fetched: proposal 18069fetched: proposal 41868
fetched: proposal 41857fetched: proposal 41859
fetched: proposal 41850
fetched: proposal 41883
fetched: proposal 41861
fetched: proposal 18052
fetched: proposal 41873
fetched: proposal 41867
fetched: proposal 41887

fetched: proposal 18047
fetched: proposal 18055fetched: proposal 18076fetched: proposal 41888
fetched: proposal 18051

fetched: proposal 41875fetched: proposal 41856

fetched: proposal 41852
fetched: proposal 41869

fetched: proposal 41876
fetched: proposal 18065
fetched: proposal 18056
fetched: proposal 41889fetched: proposal 41878
fetched: proposal 41860

fetched: proposal 18038
fetched: proposal 41899
fetched: proposal 18040
fetched: proposal 18005fetched: proposal 41864

fetched: proposal 41841
fetched: prop

In [76]:
df_wordcloud = pd.read_csv('data/topic_summary_joined.csv', index_col ="Unnamed: 0")
df_wordcloud.head()

fetched: proposal 38380
fetched: proposal 75690
fetched: proposal 38401
fetched: proposal 38392
fetched: proposal 38376
fetched: proposal 75689
fetched: proposal 38398
fetched: proposal 38396
fetched: proposal 75691
fetched: proposal 75684
fetched: proposal 75686
fetched: proposal 75688
fetched: proposal 38404
fetched: proposal 75685
fetched: proposal 75692
fetched: proposal 75687
fetched: proposal 75693
fetched: proposal 75698
fetched: proposal 75697
fetched: proposal 75703
fetched: proposal 38399
fetched: proposal 75696
fetched: proposal 75701
fetched: proposal 75695
fetched: proposal 38403
fetched: proposal 75694
fetched: proposal 38408
fetched: proposal 75705
fetched: proposal 75704
fetched: proposal 75702
fetched: proposal 75700
fetched: proposal 75699
fetched: proposal 38413
fetched: proposal 75706
fetched: proposal 75714
fetched: proposal 75708
fetched: proposal 38411
fetched: proposal 75707
fetched: proposal 75710
fetched: proposal 75713
fetched: proposal 75712
fetched: proposa

topic  \
0                TOPIC_EXCHANGE_RATE   
1                   TOPIC_GOVERNANCE   
2                          TOPIC_KYC   
3  TOPIC_NETWORK_CANISTER_MANAGEMENT   
4            TOPIC_NETWORK_ECONOMICS   

                                             summary  
0  The ICP/XDR conversion rate is set to 28.0425....  
1  SetAuthorizedSubnetworks SetAuthorizedSubnetwo...  
2  The proposal unlocks all neurons associated wi...  
3  Upgrade ledger canister to git commit 8a560f95...  
4                          ClearProvisionalWhitelist

fetched: proposal 75730
fetched: proposal 38415
fetched: proposal 38412
fetched: proposal 38432
fetched: proposal 75731

fetched: proposal 75733
fetched: proposal 75738
fetched: proposal 38416
fetched: proposal 38419
fetched: proposal 75732
fetched: proposal 38446
fetched: proposal 38414
fetched: proposal 75742
fetched: proposal 38423
fetched: proposal 75757
fetched: proposal 38442
fetched: proposal 75743
fetched: proposal 75734
fetched: proposal 75760fetched: proposal 75750

fetched: proposal 75756
fetched: proposal 75751fetched: proposal 75745

fetched: proposal 75766
fetched: proposal 75740
fetched: proposal 38455
fetched: proposal 75759


In [55]:
def generate_wordcloud(df_wordcloud, topics):

    words = []
    for topic in topics:
        words.append(
            df_wordcloud.query(f"topic == '{topic}'")['summary'].values[0]
        )

    all_words = (' ').join(words)

    with open('data/all_words.txt', 'w') as f:
        f.write(all_words)

    wc = WordCloud(
        background_color='black',
        repeat=True,
        width=1024 * 2,
        height=768 * 2,
        max_words=200,
        colormap='Set2',
        font_path='fonts/impact.ttf'
    )
    wc.generate(all_words)

    return wc

fetched: proposal 48944

fetched: proposal 22174
fetched: proposal 48909
fetched: proposal 48932
fetched: proposal 22154
fetched: proposal 48965
fetched: proposal 22137
fetched: proposal 48963
fetched: proposal 22192

fetched: proposal 48967fetched: proposal 48953
fetched: proposal 48948

fetched: proposal 48952
fetched: proposal 48950

fetched: proposal 22180
fetched: proposal 48966fetched: proposal 48968
fetched: proposal 48961
fetched: proposal 48974
fetched: proposal 48958fetched: proposal 48972fetched: proposal 48956
fetched: proposal 48936
fetched: proposal 48969fetched: proposal 48955fetched: proposal 22179



fetched: proposal 22155

fetched: proposal 48949
fetched: proposal 48971

fetched: proposal 48951
fetched: proposal 48987
fetched: proposal 48975
fetched: proposal 22151
fetched: proposal 22159
fetched: proposal 22157
fetched: proposal 22166
fetched: proposal 48976
fetched: proposal 48959
fetched: proposal 48957
fetched: proposal 48978
fetched: proposal 22164
fetched: prop

In [85]:
def generate_word_freq(df_wordcloud, topics):

    words = []
    for topic in topics:
        words.append(
            df_wordcloud.query(f"{'topic'} == '{topic}'")['summary'].values[0]
        )
    all_words = [ele for ele in words if len(ele) > 20]
    all_words = (' ').join(all_words).upper()
    all_words = regex.sub(r'\b[0-9]+\b\W*', '', all_words)
    all_words = regex.sub(r'(?:^| )\w(?:$| )', ' ', all_words)

    def replace_digit(string):
        string = regex.sub(r'\d', '', string).strip()
        return string

    all_words = all_words.upper()

    tokens = nltk.word_tokenize(all_words)
    text = nltk.Text(tokens)
    freq = nltk.Counter(text).items()
    res = []
    for item in freq:
        res.append(item)

    res.sort(key=lambda x: x[1], reverse=True)
    return res

fetched: proposal 84463
fetched: proposal 84456
fetched: proposal 84476
fetched: proposal 84455
fetched: proposal 84464
fetched: proposal 43808
fetched: proposal 43806
fetched: proposal 84495
fetched: proposal 84461
fetched: proposal 84470
fetched: proposal 84475
fetched: proposal 84493
fetched: proposal 84486
fetched: proposal 84462fetched: proposal 84457fetched: proposal 43816
fetched: proposal 43812
fetched: proposal 84492
fetched: proposal 84494
fetched: proposal 84477

fetched: proposal 84489
fetched: proposal 84479
fetched: proposal 84497
fetched: proposal 84472
fetched: proposal 84488
fetched: proposal 43804

fetched: proposal 84487
fetched: proposal 84471
fetched: proposal 84484
fetched: proposal 43817
fetched: proposal 84483fetched: proposal 84503
fetched: proposal 84502
fetched: proposal 84498
fetched: proposal 84480
fetched: proposal 43810
fetched: proposal 84491
fetched: proposal 84485
fetched: proposal 84466
fetched: proposal 84465
fetched: proposal 43780
fetched: proposal

In [88]:
find_topics = df_wordcloud.topic.unique()
find_topics

fetched: proposal 45959fetched: proposal 45986


array(['TOPIC_EXCHANGE_RATE', 'TOPIC_GOVERNANCE', 'TOPIC_KYC',
       'TOPIC_NETWORK_CANISTER_MANAGEMENT', 'TOPIC_NETWORK_ECONOMICS',
       'TOPIC_NODE_PROVIDER_REWARDS', 'TOPIC_PARTICIPANT_MANAGEMENT',
       'TOPIC_SUBNET_MANAGEMENT'], dtype=object)

fetched: proposal 88118fetched: proposal 45975
fetched: proposal 88070
fetched: proposal 88121

fetched: proposal 88125
fetched: proposal 88136
fetched: proposal 88108
fetched: proposal 45973
fetched: proposal 88132
fetched: proposal 88147
fetched: proposal 45995
fetched: proposal 88123
fetched: proposal 88119fetched: proposal 88130
fetched: proposal 88144
fetched: proposal 88086

fetched: proposal 88138fetched: proposal 45996

fetched: proposal 88120
fetched: proposal 46013
fetched: proposal 88135
fetched: proposal 88124
fetched: proposal 88145
fetched: proposal 88137
fetched: proposal 88139
fetched: proposal 88131
fetched: proposal 88152
fetched: proposal 88126
fetched: proposal 88154
fetched: proposal 88129
fetched: proposal 88128
fetched: proposal 88074
fetched: proposal 88133
fetched: proposal 88143
fetched: proposal 88142

fetched: proposal 88159
fetched: proposal 88146
fetched: proposal 45985
fetched: proposal 88148
fetched: proposal 88065
fetched: proposal 88149
fetched: propos

In [94]:
data = generate_word_freq(
    df_wordcloud=df_wordcloud,
    topics=find_topics
)

fetched: proposal 95267

fetched: proposal 95263
fetched: proposal 95278
fetched: proposal 50052
fetched: proposal 50050
fetched: proposal 50051
fetched: proposal 50065
fetched: proposal 50059
fetched: proposal 50058
fetched: proposal 50079fetched: proposal 50067
fetched: proposal 50057

fetched: proposal 50068
fetched: proposal 50063
fetched: proposal 50085
fetched: proposal 95281
fetched: proposal 95280
fetched: proposal 50072
fetched: proposal 50076
fetched: proposal 95283fetched: proposal 95285
fetched: proposal 95282
fetched: proposal 50071
fetched: proposal 95286
fetched: proposal 95287

fetched: proposal 95288
fetched: proposal 95291
fetched: proposal 50096
fetched: proposal 50080
fetched: proposal 95289
fetched: proposal 95295
fetched: proposal 95284
fetched: proposal 50075fetched: proposal 50095
fetched: proposal 50074

fetched: proposal 50099
fetched: proposal 95293fetched: proposal 95298
fetched: proposal 95290fetched: proposal 95301
fetched: proposal 95299

fetched: proposa

In [102]:
# create an empty pickle file
import os
filename = "figures/wordcloud.html"
os.makedirs(os.path.dirname(filename), exist_ok=True)

fetched: proposal 65699
fetched: proposal 65702
fetched: proposal 65708
fetched: proposal 65703
fetched: proposal 65710
fetched: proposal 65713
fetched: proposal 65716
fetched: proposal 65706
fetched: proposal 65695
fetched: proposal 65701fetched: proposal 65717
fetched: proposal 65730

fetched: proposal 65709
fetched: proposal 65718
fetched: proposal 65715
fetched: proposal 65728
fetched: proposal 65704
fetched: proposal 65720
fetched: proposal 65725
fetched: proposal 65726
fetched: proposal 65721
fetched: proposal 65722
fetched: proposal 65723
fetched: proposal 65727
fetched: proposal 65719

In [105]:
WordCloud(init_opts=opts.InitOpts()).add(
        series_name="Keywords",
        data_pair=data,
        word_size_range=[20, 80],
        textstyle_opts=opts.TextStyleOpts(
            font_family="impact",
            font_weight='bold',
            color='blue'
        ),
        rotate_step=90
    ).set_global_opts(
        # title_opts=opts.TitleOpts("Theme-dark"),
        title_opts=opts.TitleOpts(
            title="Keywords", title_textstyle_opts=opts.TextStyleOpts(font_size=23),
        ),
        tooltip_opts=opts.TooltipOpts(is_show=True),
    ).render('figures/wordcloud.html')

fetched: proposal 84941
fetched: proposal 84953
fetched: proposal 84951
fetched: proposal 84950
fetched: proposal 84944
fetched: proposal 84954fetched: proposal 84966
fetched: proposal 84945
fetched: proposal 84962

fetched: proposal 84959
fetched: proposal 84946
fetched: proposal 84969
fetched: proposal 84968
fetched: proposal 84964
fetched: proposal 84976
fetched: proposal 84960
fetched: proposal 84961
fetched: proposal 84967
fetched: proposal 84971
fetched: proposal 84980
fetched: proposal 84970
fetched: proposal 84981
fetched: proposal 84963
fetched: proposal 84982
fetched: proposal 84972
fetched: proposal 84978
fetched: proposal 84956fetched: proposal 84973
fetched: proposal 84979
fetched: proposal 84977
fetched: proposal 84965
fetched: proposal 84974
fetched: proposal 84975
fetched: proposal 84987
fetched: proposal 84983

fetched: proposal 84986
fetched: proposal 84992
fetched: proposal 84984
fetched: proposal 84991
fetched: proposal 84988
fetched: proposal 84989
fetched: proposa

'/content/drive/MyDrive/ic-gov-visualization/figures/wordcloud.html'

fetched: proposal 84996
fetched: proposal 84990
fetched: proposal 85001
fetched: proposal 85013
fetched: proposal 85000
fetched: proposal 84997
fetched: proposal 84998
fetched: proposal 85014
fetched: proposal 84995
fetched: proposal 84999
fetched: proposal 85012
fetched: proposal 85010
fetched: proposal 84994
fetched: proposal 85003
fetched: proposal 84985
fetched: proposal 85019
fetched: proposal 85011
fetched: proposal 85007


In [375]:
import IPython
IPython.display.HTML(filename='figures/wordcloud.html')

## 3.2. Topics 

In [640]:
topic_time_df = df[['proposal_id', 'topic',
                    'updated_at']].set_index('proposal_id')
topic_time_df.dtypes               

topic         object
updated_at    object
dtype: object

In [641]:
topic_time_df.columns

Index(['topic', 'updated_at'], dtype='object')

In [642]:
topic_time_df['updated_at']= pd.to_datetime(topic_time_df['updated_at']).dt.date
topic_time_df

topic  updated_at
proposal_id                                               
3            TOPIC_NETWORK_CANISTER_MANAGEMENT  2021-08-05
4            TOPIC_NETWORK_CANISTER_MANAGEMENT  2021-08-05
5            TOPIC_NETWORK_CANISTER_MANAGEMENT  2021-08-05
6            TOPIC_NETWORK_CANISTER_MANAGEMENT  2021-08-05
7            TOPIC_NETWORK_CANISTER_MANAGEMENT  2021-08-05
...                                        ...         ...
18481                      TOPIC_EXCHANGE_RATE  2021-09-02
18482                      TOPIC_EXCHANGE_RATE  2021-09-02
18483                      TOPIC_EXCHANGE_RATE  2021-09-02
18484                      TOPIC_EXCHANGE_RATE  2021-09-02
18485                      TOPIC_EXCHANGE_RATE  2021-09-02

[5535 rows x 2 columns]

In [643]:
topic_time_df['updated_at']= pd.to_datetime(topic_time_df['updated_at'])
topic_time_df


topic updated_at
proposal_id                                              
3            TOPIC_NETWORK_CANISTER_MANAGEMENT 2021-08-05
4            TOPIC_NETWORK_CANISTER_MANAGEMENT 2021-08-05
5            TOPIC_NETWORK_CANISTER_MANAGEMENT 2021-08-05
6            TOPIC_NETWORK_CANISTER_MANAGEMENT 2021-08-05
7            TOPIC_NETWORK_CANISTER_MANAGEMENT 2021-08-05
...                                        ...        ...
18481                      TOPIC_EXCHANGE_RATE 2021-09-02
18482                      TOPIC_EXCHANGE_RATE 2021-09-02
18483                      TOPIC_EXCHANGE_RATE 2021-09-02
18484                      TOPIC_EXCHANGE_RATE 2021-09-02
18485                      TOPIC_EXCHANGE_RATE 2021-09-02

[5535 rows x 2 columns]

In [644]:
topic_time_df.dtypes

topic                 object
updated_at    datetime64[ns]
dtype: object

In [ ]:
find_topics=list(topic_time_df.topic.unique())
find_topics

In [645]:
topic_time_df['updated_at'] = topic_time_df['updated_at']
topic_time_stats = topic_time_df.groupby(['updated_at','topic']).size().reset_index()
topic_time_stats.columns = ['update_at','topic','count']
topic_time_stats

update_at                              topic  count
0  2021-08-05                TOPIC_EXCHANGE_RATE    265
1  2021-08-05                   TOPIC_GOVERNANCE     80
2  2021-08-05                          TOPIC_KYC      2
3  2021-08-05  TOPIC_NETWORK_CANISTER_MANAGEMENT     44
4  2021-08-05            TOPIC_NETWORK_ECONOMICS      1
..        ...                                ...    ...
57 2021-09-01                   TOPIC_GOVERNANCE      1
58 2021-09-02                TOPIC_EXCHANGE_RATE     90
59 2022-01-27                TOPIC_EXCHANGE_RATE    862
60 2022-01-27            TOPIC_SUBNET_MANAGEMENT     54
61 2022-09-19                          TOPIC_KYC     19

[62 rows x 3 columns]

In [652]:
topic_time_stats=topic_time_stats.pivot(index='update_at', columns='topic', values='count').fillna(0).reset_index()
topic_time_stats

topic  update_at  TOPIC_EXCHANGE_RATE  TOPIC_GOVERNANCE  TOPIC_KYC  \
0     2021-08-05                265.0              80.0        2.0   
1     2021-08-06                144.0               0.0        0.0   
2     2021-08-07                144.0               0.0        0.0   
3     2021-08-08                144.0               0.0        0.0   
4     2021-08-09                144.0               0.0        0.0   
5     2021-08-10                144.0               0.0        1.0   
6     2021-08-11                144.0               0.0        0.0   
7     2021-08-12                144.0               0.0        0.0   
8     2021-08-13                144.0               0.0        0.0   
9     2021-08-14                144.0               0.0        0.0   
10    2021-08-15                144.0               0.0        0.0   
11    2021-08-16                144.0               0.0        0.0   
12    2021-08-17                145.0               0.0        0.0   
13    2021-08-18                144.0               0.0        0.0   
14    2021-08-19                144.0               0.0        0.0   
15    2021-08-20                144.0               0.0        0.0   
16    2021-08-21                144.0               0.0        0.0   
17    2021-08-22                144.0               0.0        0.0   
18    2021-08-23                144.0               0.0        1.0   
19    2021-08-24                144.0               0.0        0.0   
20    2021-08-25                145.0               0.0        0.0   
21    2021-08-26                144.0               0.0        0.0   
22    2021-08-27                144.0               0.0        0.0   
23    2021-08-28                144.0               0.0        0.0   
24    2021-08-29                144.0               0.0        0.0   
25    2021-08-30                144.0               2.0        0.0   
26    2021-08-31                146.0               1.0        0.0   
27    2021-09-01                147.0               1.0        0.0   
28    2021-09-02                 90.0               0.0        0.0   
29    2022-01-27                862.0               0.0        0.0   
30    2022-09-19                  0.0               0.0       19.0   

topic  TOPIC_NETWORK_CANISTER_MANAGEMENT  TOPIC_NETWORK_ECONOMICS  \
0                                   44.0                      1.0   
1                                    0.0                      0.0   
2                                    0.0                      0.0   
3                                    0.0                      0.0   
4                                    0.0                      0.0   
5                                    0.0                      0.0   
6                                    1.0                      0.0   
7                                    0.0                      0.0   
8                                    0.0                      0.0   
9                                    0.0                      0.0   
10                                   0.0                      0.0   
11                                   0.0                      0.0   
12                                   0.0                      0.0   
13                                   0.0                      0.0   
14                                   2.0                      0.0   
15                                   0.0                      0.0   
16                                   0.0                      0.0   
17                                   0.0                      0.0   
18                                   0.0                      0.0   
19                                   0.0                      0.0   
20                                   0.0                      0.0   
21                                   2.0                      0.0   
22                                   0.0                      0.0   
23                                   0.0                      0.0   
24                                

In [653]:
topic_time_stats.columns

Index(['update_at', 'TOPIC_EXCHANGE_RATE', 'TOPIC_GOVERNANCE', 'TOPIC_KYC',
       'TOPIC_NETWORK_CANISTER_MANAGEMENT', 'TOPIC_NETWORK_ECONOMICS',
       'TOPIC_NODE_PROVIDER_REWARDS', 'TOPIC_PARTICIPANT_MANAGEMENT',
       'TOPIC_SUBNET_MANAGEMENT'],
      dtype='object', name='topic')

In [654]:
topic_time_stats=topic_time_stats.set_index('update_at')
topic_time_stats

topic       TOPIC_EXCHANGE_RATE  TOPIC_GOVERNANCE  TOPIC_KYC  \
update_at                                                      
2021-08-05                265.0              80.0        2.0   
2021-08-06                144.0               0.0        0.0   
2021-08-07                144.0               0.0        0.0   
2021-08-08                144.0               0.0        0.0   
2021-08-09                144.0               0.0        0.0   
2021-08-10                144.0               0.0        1.0   
2021-08-11                144.0               0.0        0.0   
2021-08-12                144.0               0.0        0.0   
2021-08-13                144.0               0.0        0.0   
2021-08-14                144.0               0.0        0.0   
2021-08-15                144.0               0.0        0.0   
2021-08-16                144.0               0.0        0.0   
2021-08-17                145.0               0.0        0.0   
2021-08-18                144.0               0.0        0.0   
2021-08-19                144.0               0.0        0.0   
2021-08-20                144.0               0.0        0.0   
2021-08-21                144.0               0.0        0.0   
2021-08-22                144.0               0.0        0.0   
2021-08-23                144.0               0.0        1.0   
2021-08-24                144.0               0.0        0.0   
2021-08-25                145.0               0.0        0.0   
2021-08-26                144.0               0.0        0.0   
2021-08-27                144.0               0.0        0.0   
2021-08-28                144.0               0.0        0.0   
2021-08-29                144.0               0.0        0.0   
2021-08-30                144.0               2.0        0.0   
2021-08-31                146.0               1.0        0.0   
2021-09-01                147.0               1.0        0.0   
2021-09-02                 90.0               0.0        0.0   
2022-01-27                862.0               0.0        0.0   
2022-09-19                  0.0               0.0       19.0   

topic       TOPIC_NETWORK_CANISTER_MANAGEMENT  TOPIC_NETWORK_ECONOMICS  \
update_at                                                                
2021-08-05                               44.0                      1.0   
2021-08-06                                0.0                      0.0   
2021-08-07                                0.0                      0.0   
2021-08-08                                0.0                      0.0   
2021-08-09                                0.0                      0.0   
2021-08-10                                0.0                      0.0   
2021-08-11                                1.0                      0.0   
2021-08-12                                0.0                      0.0   
2021-08-13                                0.0                      0.0   
2021-08-14                                0.0                      0.0   
2021-08-15                                0.0                      0.0   
2021-08-16                                0.0                      0.0   
2021-08-17                                0.0                      0.0   
2021-08-18                                0.0                      0.0   
2021-08-19                                2.0                      0.0   
2021-08-20                                0.0                      0.0   
2021-08-21                                0.0                      0.0   
2021-08-22                                0.0                      0.0   
2021-08-23                                0.0                      0.0   
2021-08-24                                0.0                      0.0   
2021-08-25                                0.0                      0.0   
2021-08-26                                2.0                      0.0   
2021-08-27                                0.0                      0.0   
2021-08-28                           

In [657]:
all_days = pd.date_range(df.index.min(), df.index.max(), freq='D')
topic_time_stats=topic_time_stats.reindex(all_days).fillna(0)
topic_time_stats

topic       TOPIC_EXCHANGE_RATE  TOPIC_GOVERNANCE  TOPIC_KYC  \
2021-08-05                265.0              80.0        2.0   
2021-08-06                144.0               0.0        0.0   
2021-08-07                144.0               0.0        0.0   
2021-08-08                144.0               0.0        0.0   
2021-08-09                144.0               0.0        0.0   
...                         ...               ...        ...   
2022-09-15                  0.0               0.0        0.0   
2022-09-16                  0.0               0.0        0.0   
2022-09-17                  0.0               0.0        0.0   
2022-09-18                  0.0               0.0        0.0   
2022-09-19                  0.0               0.0       19.0   

topic       TOPIC_NETWORK_CANISTER_MANAGEMENT  TOPIC_NETWORK_ECONOMICS  \
2021-08-05                               44.0                      1.0   
2021-08-06                                0.0                      0.0   
2021-08-07                                0.0                      0.0   
2021-08-08                                0.0                      0.0   
2021-08-09                                0.0                      0.0   
...                                       ...                      ...   
2022-09-15                                0.0                      0.0   
2022-09-16                                0.0                      0.0   
2022-09-17                                0.0                      0.0   
2022-09-18                                0.0                      0.0   
2022-09-19                                0.0                      0.0   

topic       TOPIC_NODE_PROVIDER_REWARDS  TOPIC_PARTICIPANT_MANAGEMENT  \
2021-08-05                          1.0                           1.0   
2021-08-06                          0.0                           0.0   
2021-08-07                          0.0                           0.0   
2021-08-08                          0.0                           0.0   
2021-08-09                          0.0                           0.0   
...                                 ...                           ...   
2022-09-15                          0.0                           0.0   
2022-09-16                          0.0                           0.0   
2022-09-17                          0.0                           0.0   
2022-09-18                          0.0                           0.0   
2022-09-19                          0.0                           0.0   

topic       TOPIC_SUBNET_MANAGEMENT  
2021-08-05                     37.0  
2021-08-06                      8.0  
2021-08-07                      0.0  
2021-08-08                      0.0  
2021-08-09                      1.0  
...                             ...  
2022-09-15                      0.0  
2022-09-16                      0.0  
2022-09-17                      0.0  
2022-09-18                      0.0  
2022-09-19                      0.0  

[411 rows x 8 columns]

In [664]:
topic_time_stats['update_at'] = topic_time_stats.index
topic_time_stats.reset_index()

topic      index  TOPIC_EXCHANGE_RATE  TOPIC_GOVERNANCE  TOPIC_KYC  \
0     2021-08-05                265.0              80.0        2.0   
1     2021-08-06                144.0               0.0        0.0   
2     2021-08-07                144.0               0.0        0.0   
3     2021-08-08                144.0               0.0        0.0   
4     2021-08-09                144.0               0.0        0.0   
..           ...                  ...               ...        ...   
406   2022-09-15                  0.0               0.0        0.0   
407   2022-09-16                  0.0               0.0        0.0   
408   2022-09-17                  0.0               0.0        0.0   
409   2022-09-18                  0.0               0.0        0.0   
410   2022-09-19                  0.0               0.0       19.0   

topic  TOPIC_NETWORK_CANISTER_MANAGEMENT  TOPIC_NETWORK_ECONOMICS  \
0                                   44.0                      1.0   
1                                    0.0                      0.0   
2                                    0.0                      0.0   
3                                    0.0                      0.0   
4                                    0.0                      0.0   
..                                   ...                      ...   
406                                  0.0                      0.0   
407                                  0.0                      0.0   
408                                  0.0                      0.0   
409                                  0.0                      0.0   
410                                  0.0                      0.0   

topic  TOPIC_NODE_PROVIDER_REWARDS  TOPIC_PARTICIPANT_MANAGEMENT  \
0                              1.0                           1.0   
1                              0.0                           0.0   
2                              0.0                           0.0   
3                              0.0                           0.0   
4                              0.0                           0.0   
..                             ...                           ...   
406                            0.0                           0.0   
407                            0.0                           0.0   
408                            0.0                           0.0   
409                            0.0                           0.0   
410                            0.0                           0.0   

topic  TOPIC_SUBNET_MANAGEMENT  update_at  
0                         37.0 2021-08-05  
1                          8.0 2021-08-06  
2                          0.0 2021-08-07  
3                          0.0 2021-08-08  
4                          1.0 2021-08-09  
..                         ...        ...  
406                        0.0 2022-09-15  
407                        0.0 2022-09-16  
408                        0.0 2022-09-17  
409                        0.0 2022-09-18  
410                        0.0 2022-09-19  

[411 rows x 10 columns]

In [672]:
topic_time_stats=pd.melt(topic_time_stats, id_vars='update_at', value_vars=find_topics)

In [673]:
topic_time_stats

update_at                              topic  value
0     2021-08-05  TOPIC_NETWORK_CANISTER_MANAGEMENT   44.0
1     2021-08-06  TOPIC_NETWORK_CANISTER_MANAGEMENT    0.0
2     2021-08-07  TOPIC_NETWORK_CANISTER_MANAGEMENT    0.0
3     2021-08-08  TOPIC_NETWORK_CANISTER_MANAGEMENT    0.0
4     2021-08-09  TOPIC_NETWORK_CANISTER_MANAGEMENT    0.0
...          ...                                ...    ...
3283  2022-09-15                TOPIC_EXCHANGE_RATE    0.0
3284  2022-09-16                TOPIC_EXCHANGE_RATE    0.0
3285  2022-09-17                TOPIC_EXCHANGE_RATE    0.0
3286  2022-09-18                TOPIC_EXCHANGE_RATE    0.0
3287  2022-09-19                TOPIC_EXCHANGE_RATE    0.0

[3288 rows x 3 columns]

In [674]:
topic_time_stats.columns

Index(['update_at', 'topic', 'value'], dtype='object')

In [677]:
topic_time_stats['update_at']=pd.to_datetime(topic_time_stats['update_at']).dt.strftime('%Y-%m-%d')


In [678]:
topic_time_stats.columns 

Index(['update_at', 'topic', 'value'], dtype='object')

In [679]:
topic_time_stats.columns = ['order','name','value']

In [683]:
topic_time_stats['value'] = topic_time_stats['value'].astype('float')
topic_time_stats.dtypes

order     object
name      object
value    float64
dtype: object

In [690]:
topic_time_stats=topic_time_stats.sort_values(by=['order'])
topic_time_stats

order                               name  value
0     2021-08-05  TOPIC_NETWORK_CANISTER_MANAGEMENT   44.0
411   2021-08-05                   TOPIC_GOVERNANCE   80.0
1644  2021-08-05            TOPIC_NETWORK_ECONOMICS    1.0
822   2021-08-05            TOPIC_SUBNET_MANAGEMENT   37.0
2877  2021-08-05                TOPIC_EXCHANGE_RATE  265.0
...          ...                                ...    ...
2876  2022-09-19       TOPIC_PARTICIPANT_MANAGEMENT    0.0
2465  2022-09-19        TOPIC_NODE_PROVIDER_REWARDS    0.0
1643  2022-09-19                          TOPIC_KYC   19.0
2054  2022-09-19            TOPIC_NETWORK_ECONOMICS    0.0
3287  2022-09-19                TOPIC_EXCHANGE_RATE    0.0

[3288 rows x 3 columns]

In [703]:
import plotly.express as px
fig = px.area(topic_time_stats, x="order", y="value", color='name',groupnorm='fraction')
fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)
fig.show()

In [702]:
import plotly.express as px
fig = px.area(topic_time_stats, x="order", y="value", color='name',groupnorm='percent')
# Add range slider
fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)
fig.show()

In [701]:
import plotly.express as px
fig = px.area(topic_time_stats, x="order", y="value", color='name',groupnorm='')
fig.show()

## 3.3. Network

In [329]:
proposer_network = df[['proposal_id', 'proposer',
                       'known_neurons_ballots', 'updated_at']]
proposer_network

proposal_id  proposer  \
30            220        35   
31            275        46   
32            293        16   
33            302        46   
34            340        32   
...           ...       ...   
5530        18481        25   
5531        18482        24   
5532        18483        22   
5533        18484        23   
5534        18485        26   

                                  known_neurons_ballots  \
30    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
31    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
32    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
33    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
34    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
...                                                 ...   
5530  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5531  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5532  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5533  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5534  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   

                      updated_at  
30    2021-08-05 15:50:43.181794  
31    2021-08-05 15:50:43.182720  
32    2021-08-05 15:50:43.183702  
33    2021-08-05 15:50:43.184697  
34    2022-09-19 11:25:17.968424  
...                          ...  
5530  2021-09-02 14:11:12.273111  
5531  2021-09-02 14:21:12.170443  
5532  2021-09-02 14:31:12.267709  
5533  2021-09-02 14:41:12.157442  
5534  2021-09-02 14:51:12.152028  

[5505 rows x 4 columns]

In [330]:
proposer_network['known_neurons_ballots'] = proposer_network['known_neurons_ballots'].map(lambda x: x.lstrip('[').rstrip(']'))
proposer_network

proposal_id  proposer  \
30            220        35   
31            275        46   
32            293        16   
33            302        46   
34            340        32   
...           ...       ...   
5530        18481        25   
5531        18482        24   
5532        18483        22   
5533        18484        23   
5534        18485        26   

                                  known_neurons_ballots  \
30    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
31    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
32    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
33    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
34    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
...                                                 ...   
5530  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5531  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5532  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5533  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5534  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   

                      updated_at  
30    2021-08-05 15:50:43.181794  
31    2021-08-05 15:50:43.182720  
32    2021-08-05 15:50:43.183702  
33    2021-08-05 15:50:43.184697  
34    2022-09-19 11:25:17.968424  
...                          ...  
5530  2021-09-02 14:11:12.273111  
5531  2021-09-02 14:21:12.170443  
5532  2021-09-02 14:31:12.267709  
5533  2021-09-02 14:41:12.157442  
5534  2021-09-02 14:51:12.152028  

[5505 rows x 4 columns]

In [331]:
proposer_network = proposer_network[proposer_network['known_neurons_ballots'].apply(len)!=0]
proposer_network['proposer'] = proposer_network['proposer'].astype(int)
proposer_network

proposal_id  proposer  \
30            220        35   
31            275        46   
32            293        16   
33            302        46   
34            340        32   
...           ...       ...   
5530        18481        25   
5531        18482        24   
5532        18483        22   
5533        18484        23   
5534        18485        26   

                                  known_neurons_ballots  \
30    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
31    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
32    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
33    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
34    {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
...                                                 ...   
5530  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5531  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5532  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5533  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   
5534  {'id': '27', 'name': 'DFINITY Foundation', 'vo...   

                      updated_at  
30    2021-08-05 15:50:43.181794  
31    2021-08-05 15:50:43.182720  
32    2021-08-05 15:50:43.183702  
33    2021-08-05 15:50:43.184697  
34    2022-09-19 11:25:17.968424  
...                          ...  
5530  2021-09-02 14:11:12.273111  
5531  2021-09-02 14:21:12.170443  
5532  2021-09-02 14:31:12.267709  
5533  2021-09-02 14:41:12.157442  
5534  2021-09-02 14:51:12.152028  

[5505 rows x 4 columns]

In [334]:
# build proposer roster
voters = proposer_network['known_neurons_ballots'].values.flatten()
voters_temp = set()
voters_id = set()
for voter_group in tqdm(voters):
    voter_group = ast.literal_eval(voter_group)
    for voter in voter_group:
        voters_id.add(int(voter.get('id')))
        voter = (voter.get('id'), voter.get('name'))
        voters_temp.add(voter)

voters = voters_temp

proposer_set = set()
for proposal in proposer_network.itertuples():
    proposer_id = proposal.proposer
    proposer_set.add(int(proposer_id))


100%|██████████| 5505/5505 [00:00<00:00, 8333.96it/s]


In [335]:
voters

{('27', 'DFINITY Foundation'), ('28', 'Internet Computer Association')}

In [336]:
proposer_set

{16,
 22,
 23,
 24,
 25,
 26,
 31,
 32,
 33,
 35,
 38,
 39,
 40,
 46,
 47,
 48,
 50,
 62,
 148885932052941248,
 1947868782075274240,
 3306538665277646848,
 9014191754770651136}

In [337]:
network_df = pd.DataFrame(0, columns=list(voters_id), index=list(proposer_set))
network_df

27  28
1947868782075274240   0   0
3306538665277646848   0   0
9014191754770651136   0   0
16                    0   0
22                    0   0
23                    0   0
24                    0   0
25                    0   0
26                    0   0
31                    0   0
32                    0   0
33                    0   0
35                    0   0
38                    0   0
39                    0   0
40                    0   0
46                    0   0
47                    0   0
48                    0   0
50                    0   0
62                    0   0
148885932052941248    0   0

In [517]:
import ast

In [518]:
for proposal in tqdm(proposer_network.itertuples(), total=len(proposer_network)):
    voters = proposal.known_neurons_ballots
    proposer_id = int(proposal.proposer)
    voters = ast.literal_eval(voters)
    for voter in voters:
        voter_id = int(voter.get('id'))
        vote = voter.get('vote')
        network_df.loc[proposer_id, voter_id] += 1


100%|██████████| 5505/5505 [00:02<00:00, 1877.80it/s]


In [519]:
network_df

27      28
1947868782075274240     4.0     4.0
3306538665277646848     2.0     2.0
9014191754770651136    50.0    50.0
16                      8.0     8.0
22                   2044.0  2044.0
23                   2046.0  2046.0
24                   2042.0  2042.0
25                   2046.0  2046.0
26                   2046.0  2046.0
31                     40.0    40.0
32                      6.0     6.0
33                      2.0     2.0
35                     32.0    32.0
38                    218.0   218.0
39                    146.0   146.0
40                    154.0   154.0
46                     20.0    20.0
47                     66.0    66.0
48                     18.0    18.0
50                     16.0    16.0
62                      2.0     2.0
148885932052941248      2.0     2.0

### 3.3.1. Heatmap

In [514]:
col_names

['voter 27', 'voter 28']

In [515]:
network_df = network_df.astype(float)
row_names = ('proposer'+' '+ network_df.index.astype('str')).to_list()
col_names = ('voter'+' '+ network_df.columns.astype('str')).to_list()
network_matrix=network_df.values.tolist()
network_matrix

[[2.0, 2.0],
 [1.0, 1.0],
 [25.0, 25.0],
 [4.0, 4.0],
 [1022.0, 1022.0],
 [1023.0, 1023.0],
 [1021.0, 1021.0],
 [1023.0, 1023.0],
 [1023.0, 1023.0],
 [20.0, 20.0],
 [3.0, 3.0],
 [1.0, 1.0],
 [16.0, 16.0],
 [109.0, 109.0],
 [73.0, 73.0],
 [77.0, 77.0],
 [10.0, 10.0],
 [33.0, 33.0],
 [9.0, 9.0],
 [8.0, 8.0],
 [1.0, 1.0],
 [1.0, 1.0]]

In [516]:
import plotapi
plotapi.api_key("b0368160-7e02-4566-9dec-1829bd5b070b")
from plotapi import HeatMap
HeatMap(network_matrix,row_names=row_names, col_names=col_names).show()

Your PlotAPI API key has been saved in your local environment. You will not need to set it again.


#

### 3.3.2 Chord Chart

In [425]:
links = []
nodes = []

for item in network_df.itertuples():
    proposer = f'Proposer {item.Index}'
    nodes.append(dict(
        name=proposer,
        group='left'
    ))
    for voter in network_df.columns:
        amount = int(network_df.loc[item.Index, voter])
        voter = f'Voter {voter}'
        links.append(dict(
                source=voter,
                target=proposer,
                value=amount
        ))

for voter in network_df.columns:
    voter = f'Voter {voter}'
    nodes.append(dict(
        name=voter,
        group='right'
    ))


In [460]:
# https://plotapi.com/gallery/posts/chord/bipartite-divided-labels/
import plotapi
plotapi.api_key("b0368160-7e02-4566-9dec-1829bd5b070b")
from plotapi import SplitChord
SplitChord(links,nodes,color='cool',node_font_size=2).show()

Your PlotAPI API key has been saved in your local environment. You will not need to set it again.


In [444]:
SplitChord(links,nodes,color='cool',node_font_size=8).to_html('figures/chord.html')

In [445]:
import IPython
IPython.display.HTML(filename='figures/chord.html')

### 3.3.3 Sankey

In [432]:
links

[{'source': 'Voter 27', 'target': 'Proposer 1947868782075274240', 'value': 2},
 {'source': 'Voter 28', 'target': 'Proposer 1947868782075274240', 'value': 2},
 {'source': 'Voter 27', 'target': 'Proposer 3306538665277646848', 'value': 1},
 {'source': 'Voter 28', 'target': 'Proposer 3306538665277646848', 'value': 1},
 {'source': 'Voter 27', 'target': 'Proposer 9014191754770651136', 'value': 25},
 {'source': 'Voter 28', 'target': 'Proposer 9014191754770651136', 'value': 25},
 {'source': 'Voter 27', 'target': 'Proposer 16', 'value': 4},
 {'source': 'Voter 28', 'target': 'Proposer 16', 'value': 4},
 {'source': 'Voter 27', 'target': 'Proposer 22', 'value': 1022},
 {'source': 'Voter 28', 'target': 'Proposer 22', 'value': 1022},
 {'source': 'Voter 27', 'target': 'Proposer 23', 'value': 1023},
 {'source': 'Voter 28', 'target': 'Proposer 23', 'value': 1023},
 {'source': 'Voter 27', 'target': 'Proposer 24', 'value': 1021},
 {'source': 'Voter 28', 'target': 'Proposer 24', 'value': 1021},
 {'source'

In [443]:
# https://datacrayon.com/posts/plotapi/sankey/customising-the-nodes/
import plotapi
plotapi.api_key("b0368160-7e02-4566-9dec-1829bd5b070b")
from plotapi import Sankey
Sankey(links, node_font_size=8).show()

Your PlotAPI API key has been saved in your local environment. You will not need to set it again.


### 3.3.4 Terminus

In [383]:
few_links = list(filter(lambda x: x['value'] > 1000, links))

In [404]:
Terminus(
    few_links,
    show_stats=False
).to_html('figures/terminus.html')

In [430]:
import IPython
IPython.display.HTML(filename='figures/terminus.html')

## 3.4: Proposal Summary Network

In [391]:
df = pd.read_pickle("proposals_no_empty.pkl")
df

action   action_nns_function  deadline_timestamp_seconds  \
0     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
1     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
2     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
3     ExecuteNnsFunction        NnsRootUpgrade                         NaN   
4     ExecuteNnsFunction    NnsCanisterUpgrade                         NaN   
...                  ...                   ...                         ...   
5530  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5531  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5532  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5533  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   
5534  ExecuteNnsFunction  IcpXdrConversionRate                         NaN   

      decided_timestamp_seconds  executed_timestamp_seconds  \
0                    1620340878                  1620340878   
1                    1620340965                  1620340965   
2                    1620341025                  1620341025   
3                    1620341096                  1620341110   
4                    1620341144                  1620341144   
...                         ...                         ...   
5530                 1630591822                  1630591822   
5531                 1630592475                  1630592475   
5532                 1630593020                  1630593020   
5533                 1630593622                  1630593622   
5534                 1630594275                  1630594275   

      failed_timestamp_seconds    id  \
0                          0.0     1   
1                          0.0     2   
2                          0.0     3   
3                          0.0     4   
4                          0.0     5   
...                        ...   ...   
5530                       0.0  4829   
5531                       0.0  4830   
5532                       0.0  4831   
5533                       0.0  4832   
5534                       0.0  4833   

                                  known_neurons_ballots  \
0                                                    []   
1                                                    []   
2                                                    []   
3                                                    []   
4                                                    []   
...                                                 ...   
5530  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5531  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5532  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5533  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   
5534  [{'id': '27', 'name': 'DFINITY Foundation', 'v...   

                                           latest_tally  \
0     {'no': 0, 'timestamp_seconds': 1620340878, 'to...   
1     {'no': 0, 'timestamp_seconds': 1620340965, 'to...   
2     {'no': 0, 'timestamp_seconds': 1620341025, 'to...   
3     {'no': 0, 'timestamp_seconds': 1620341096, 'to...   
4     {'no': 0, 'timestamp_seconds': 1620341144, 'to...   
...                                                 ...   
5530  {'no': 0, 'timestamp_seconds': 1630591822, 'to...   
5531  {'no': 0, 'timestamp_seconds': 1630592475, 'to...   
5532  {'no': 0, 'timestamp_seconds': 1630593020, 'to...   
5533  {'no': 0, 'timestamp_seconds': 1630593622, 'to...   
5534  {'no': 0, 'timestamp_seconds': 1630594275, 'to...   

                                                payload  ...  proposer  \
0     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
1     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
2     {'arg': [], 'authz_changes': [], 'canister_id'...  ...        35   
3                                                    {}  ...        35   
4     {'arg': [], 'authz_changes': [], 'canister_id'...

In [392]:
df_network = df[df['topic'] != 'TOPIC_EXCHANGE_RATE']['summary']

In [393]:
network_all_words = ('. '.join(list(df_network.values)))
network_all_words = regex.sub(r'\b[0-9]+\b\W*', '', network_all_words)
network_all_words = regex.sub(r'(?:^| )\w(?:$| )', ' ', network_all_words)

In [394]:
def remove_url(txt):
    url_pattern = regex.compile(r'https?://\S+|www\.\S+')
    no_url = url_pattern.sub(r'', txt)

    return no_url


def stem_tokens(tokens):
    stemmer = nltk.stem.PorterStemmer()
    tokens = [stemmer.stem(token) for token in tokens]
    return tokens


def lemmatize_tokens(tokens):
    lemmatizer = nltk.stem.WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(token) for token in tokens]
    return tokens


In [398]:
text_no_urls = remove_url(network_all_words)
text_no_urls = text_no_urls.encode('utf-8', errors='ignore').decode('utf-8')
words_in_text = text_no_urls.split()
stop_words = set(stopwords.words('english'))
words_nsw = [word for word in words_in_text if not word in stop_words]
words_nsw = [ele for ele in words_nsw if len(ele) < 20]


In [399]:
import nltk
nltk.download('wordnet')
nltk.download('omw-1.4')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

In [400]:
lemmatizer = WordNetLemmatizer()
words_nsw_nc = [lemmatizer.lemmatize(w) for w in words_nsw]
words_nsw_nc = [
    word for word in words_nsw_nc if word not in string.punctuation]

In [401]:
bigram = list(nltk.bigrams(words_nsw_nc))
bigram_counts = collections.Counter(bigram).most_common(100)

In [402]:
G = nx.Graph()
for edge in bigram_counts:
    link = edge[0]
    count = edge[1]
    
    G.add_edge(link[0], link[1], weight=count)

In [403]:
fig = ig.plot(
    G,
    node_opacity=0.8,
)
fig.update_layout(
    dict(
        width=800,
        height=600,
    )
)

with open('figures/network.html', 'w') as f:
    f.write(fig.to_html())

fig.show()
